# EDA - France

## Preparation

In [1]:
import pathlib
import itertools
import numpy
import pandas

from bokeh.layouts import column
from bokeh.models import ColumnDataSource, RangeTool, HoverTool
from bokeh.plotting import figure, show
from bokeh.palettes import Viridis11

In [2]:
from bokeh.io import output_notebook
output_notebook()

Loading BokehJS ...

## Get Data

In [3]:
df = pandas.read_excel(io = pathlib.Path('../data/processed/france.xlsx'))

## Split for Easy Analysis

In [4]:
df_unemployment_rate_compare = df[['Time', 'Unemployment_Rate_TOT', 'Labor_Markets|Unemployment_Rate|Percent']]

df_unemployment_rate = df[['Time', 'Unemployment_Rate_MEN', 'Unemployment_Rate_TOT','Unemployment_Rate_WOMEN']]

df_electricity = df[['Time', 'Electricity_Distribution_Losses', 'Electricity_Final_Consumption_(Calculated)']]
df_natural_trade_balance = df[['Time', 'Natural_Gas_Trade_Balance']]

df_production = df[['Time',
    'Economic_Activity|Industrial_Production|Index|Base_Year-2010=100',
    'Economic_Activity|Industrial_Production|Manufacturing|Index|Base_Year-2010=100',
    'Industrial_Production|Seasonally_adjusted|Index|Base_Year-2010=100']]
df_prices = df[['Time', 'Financial_Market_Prices|Equities|Index|Base_Year-None',
    'Prices|Consumer_Price_Index|All_items|Index|Base_Year-2010=100',
    'Prices|Producer_Price_Index|All_Commodities|Index|Base_Year-2010=100']]
df_labour = df[['Time', 'Labor_Markets|Unemployment_Rate|Percent',
    'Labor_Markets|Wage_Rates|Index', 'Unemployment|Persons|Number_of']]

df_gdp_current_unadjusted = df[['Time', 'Change_in_Inventories|Nominal|Undjusted|Domestic_Currency',
    'Exports_of_Goods_and_Services|Nominal|Undjusted|Domestic_Currency',
    'Government_Consumption_Expenditure|Nominal|Undjusted|Domestic_Currency',
    'Gross_Domestic_Product|Nominal|Undjusted|Domestic_Currency',
    'Gross_Fixed_Capital_Formation|Nominal|Undjusted|Domestic_Currency',
    'Household_Consumption_Expenditure|incl._NPISHs|Nominal|Undjusted|Domestic_Currency',
    'Imports_of_Goods_and_Services|Nominal|Undjusted|Domestic_Currency']]
df_gdp_current_adjusted = df[['Time',
    'Change_in_Inventories|Nominal|Seasonally_Adjusted|Domestic_Currency',
    'Exports_of_Goods_and_Services|Nominal|Seasonally_Adjusted|Domestic_Currency',
    'Government_Final_Consumption_Expenditure|Nominal|Seasonally_adjusted|Domestic_Currency',
    'Gross_Domestic_Product|Nominal|Seasonally_Adjusted|Domestic_Currency',
    'Gross_Fixed_Capital_Formation|Nominal|Seasonally_Adjusted|Domestic_Currency',
    'Household_Consumption_Expenditure|incl._NPISHs|Nominal|Seasonally_Adjusted|Domestic_Currency',
    'Imports_of_Goods_and_Services|Nominal|Seasonally_Adjusted|Domestic_Currency']]

df_gdp_constant_unadjusted = df[['Time',
    'Change_in_Inventories|Real|Undjusted|Domestic_Currency|Base_Year-2010.0',
    'Exports_of_Goods_and_Services|Real|Undjusted|Domestic_Currency|Base_Year-2010.0',
    'Government_Consumption_Expenditure|Real|Undjusted|Domestic_Currency|Base_Year-2010.0',
    'Gross_Domestic_Product|Real|Undjusted|Domestic_Currency|Base_Year-2010.0',
    'Gross_Fixed_Capital_Formation|Real|Undjusted|Domestic_Currency|Base_Year-2010.0',
    'Household_Consumption_Expenditure|incl._NPISHs|Real|Undjusted|Domestic_Currency|Base_Year-2010.0',
    'Imports_of_Goods_and_Services|Real|Undjusted|Domestic_Currency|Base_Year-2010.0']]
df_gdp_constant_adjusted = df[['Time',
    'Change_in_Inventories|Real|Seasonally_Adjusted|Domestic_Currency|Base_Year-2010.0',
    'Exports_of_Goods_and_Services|Real|Seasonally_Adjusted|Domestic_Currency|Base_Year-2010.0',
    'Government_Final_Consumption_Expenditure|Real|Seasonally_adjusted|Domestic_Currency|Base_Year-2010.0',
    'Gross_Domestic_Product|Deflator|Seasonally_Adjusted|Base_Year-2010.0',
    'Gross_Domestic_Product|Real|Seasonally_Adjusted|Domestic_Currency|Base_Year-2010.0',
    'Gross_Fixed_Capital_Formation|Real|Seasonally_Adjusted|Domestic_Currency|Base_Year-2010.0',
    'Household_Consumption_Expenditure|incl._NPISHs|Real|Seasonally_Adjusted|Domestic_Currency|Base_Year-2010.0',
    'Imports_of_Goods_and_Services|Real|Seasonally_Adjusted|Domestic_Currency|Base_Year-2010.0']]

df_confidence = df[['Time', 'Business_Confidence', 'Consumer_Confidence']]

df_interest_rates = df[['Time', 'Deposit_Rate', 'Government_Bonds',
    'Harmonized_Euro_Area_Rates|Loans|Households|Consumer_Credit_and_Other|Up_to_1_Year',
    'Harmonized_Euro_Area_Rates|Loans|Households|House_Purchase|Over_5_Years',
    'Harmonized_Euro_Area_Rates|Loans|Non-Financial_Corporations|Up_to_1_Year',
    'Harmonized_Euro_Area_Rates|New_Business|Deposits|Households|Agreed_Maturity|Up_to_1_Year',
    'Harmonized_Euro_Area_Rates|New_Business|Deposits|Non-financial_Corporations|Agreed_Maturity|Up_to_1_Year',
    'Harmonized_Euro_Area_Rates|New_Business|Loans|Households|Consumption|Floating_Rate_and_up_to_1_Year',
    'Harmonized_Euro_Area_Rates|New_Business|Loans|Households|House_Purchase|Over_5_Years',
    'Harmonized_Euro_Area_Rates|Outstanding_Amounts|Deposits|Households|Agreed_Maturity|Up_to_2_Years',
    'Harmonized_Euro_Area_Rates|Outstanding_Amounts|Deposits|Non-Financial_Corporations|Agreed_Maturity|Up_to_2_Years']]

## Common Preparation for Figures

In [5]:
dates = numpy.array(df['Time'], dtype=numpy.datetime64)

source = ColumnDataSource(data=df)

figure_args = {'height': 300, 'width': 800, 
    'tools': 'pan,wheel_zoom,reset,crosshair', 'toolbar_location': 'right',
    'x_axis_type': 'datetime', 'x_axis_location': 'above', 
    'background_fill_color': '#efefef'
}

select_tool_args = {
    'title': 'Drag the middle and edges of the selection box to change the range above',
    'height': 130, 'width': 800,
    'x_axis_type': 'datetime', 'y_axis_type': None,
    'tools': '', 'toolbar_location': None, 
    'background_fill_color': '#efefef'
}

colors = itertools.cycle(Viridis11)

line_args = {
    'source': source,
    'line_color': next(colors),
    'muted_alpha': 0.4
}

## Figures

### Unemployment Rates from Various Sources

In [6]:
p = figure(**figure_args, 
    title = 'Unemployment Rates',
    y_axis_label = 'Percentage',
    x_range = (dates[500], dates[602]),
)
p.line('Time', 'Unemployment_Rate_TOT', legend_label = 'Unemployment Rate: OECD', **line_args)
p.line('Time', 'Labor_Markets|Unemployment_Rate|Percent', legend_label = 'Unemployment Rate: IMF', muted = True, **line_args)

p.legend.location = "top_right"
p.legend.click_policy="mute"

hover_tool = HoverTool(
    mode = 'vline',
    tooltips = [
        ('Time-Period', '@Time{%m/%Y}'),
        ('OECD', '@Unemployment_Rate_TOT'),
        ('IMF', '@{Labor_Markets|Unemployment_Rate|Percent}')
    ],
    formatters = {'@Time': 'datetime'}
)
p.add_tools(hover_tool)

select = figure(**select_tool_args)
select.line('Time', 'Unemployment_Rate_TOT', source=source)
select.ygrid.grid_line_color = None

range_tool = RangeTool(x_range=p.x_range)
range_tool.overlay.fill_color = 'navy'
range_tool.overlay.fill_alpha = 0.2
select.add_tools(range_tool)

show(column(p, select))

### Vs. Energy

#### Vs. Electricity

In [7]:
p2 = figure(**figure_args, 
    title = 'Electricity',
    y_axis_label = 'GigaWattHours',
    x_range = p.x_range
)
p2.line('Time', 'Electricity_Distribution_Losses', legend_label = 'Distribution Losses', **line_args)
p2.line('Time', 'Electricity_Final_Consumption_(Calculated)', legend_label = 'Total Consumption', **line_args)

p2.legend.location = 'top_right'
p2.legend.click_policy = 'mute'

h2 = HoverTool(
    mode = 'vline',
    tooltips = [
        ('Time-Period', '@Time{%m/%Y}'),
        ('Distribution Losses', '@Electricity_Distribution_Losses'),
        ('Total Consumption', '@{Electricity_Final_Consumption_(Calculated)}')
    ],
    formatters = {'@Time': 'datetime'}
)
p2.add_tools(h2)

show(column(p, p2, select))

#### Vs. Gas Trade Balance

In [8]:
p3 = figure(**figure_args, 
    title = 'Gas Trade Balance',
    y_axis_label = 'Million Meter Cube',
    x_range = p.x_range
)
p3.line('Time', 'Natural_Gas_Trade_Balance', legend_label = 'Gas Trade Balance', **line_args)

p3.legend.location = 'top_right'
p3.legend.click_policy = 'mute'

h3 = HoverTool(
    mode = 'vline',
    tooltips = [
        ('Time-Period', '@Time{%m/%Y}'),
        ('Gas Trade Balance', '@Natural_Gas_Trade_Balance'),
    ],
    formatters = {'@Time': 'datetime'}
)
p3.add_tools(h3)

show(column(p, p3, select))

### Vs. Prices, Production, Labour and Interest Rates

#### Vs. Prices

In [9]:
p4 = figure(**figure_args, 
    title = 'Price Indices',
    y_axis_label = 'Indices',
    x_range = p.x_range
)
p4.line('Time', 'Financial_Market_Prices|Equities|Index|Base_Year-None', legend_label = 'Equity Prices', **line_args)
p4.line('Time', 'Prices|Consumer_Price_Index|All_items|Index|Base_Year-2010=100', legend_label = 'Consumer Price Index (Base Year 2010)', **line_args)
p4.line('Time', 'Prices|Producer_Price_Index|All_Commodities|Index|Base_Year-2010=100', legend_label = 'Producer Price Index (Base Year 2010)', **line_args)

p4.legend.location = 'top_right'
p4.legend.click_policy = 'mute'

h4 = HoverTool(
    mode = 'vline',
    tooltips = [
        ('Time-Period', '@Time{%m/%Y}'),
        ('Equity Prices', '@{Financial_Market_Prices|Equities|Index|Base_Year-None}'),
        ('Consumer Price Index (Base Year 2010)', '@{Prices|Consumer_Price_Index|All_items|Index|Base_Year-2010=100}'),
        ('Producer Price Index (Base Year 2010)', '@{Prices|Producer_Price_Index|All_Commodities|Index|Base_Year-2010=100}')
    ],
    formatters = {'@Time': 'datetime'}
)
p4.add_tools(h4)

show(column(p, p4, select))

#### Vs. Production

In [11]:
p5 = figure(**figure_args, 
    title = 'Production Indices',
    y_axis_label = 'Indices',
    x_range = p.x_range
)
p5.line('Time', 'Economic_Activity|Industrial_Production|Index|Base_Year-2010=100', legend_label = 'Economic, Production', **line_args)
p5.line('Time', 'Economic_Activity|Industrial_Production|Manufacturing|Index|Base_Year-2010=100', legend_label = 'Economic, Production, Manufacturing', **line_args)
p5.line('Time', 'Industrial_Production|Seasonally_adjusted|Index|Base_Year-2010=100', legend_label = 'Production (Seasonally Adjusted)', **line_args)

p5.legend.location = 'top_right'
p5.legend.click_policy = 'mute'

h5 = HoverTool(
    mode = 'vline',
    tooltips = [
        ('Time-Period', '@Time{%m/%Y}'),
        ('Economic, Production', '@{Economic_Activity|Industrial_Production|Index|Base_Year-2010=100}'),
        ('Economic, Production, Manufacturing', '@{Economic_Activity|Industrial_Production|Manufacturing|Index|Base_Year-2010=100}'),
        ('Production (Seasonally Adjusted)', '@{Industrial_Production|Seasonally_adjusted|Index|Base_Year-2010=100}')
    ],
    formatters = {'@Time': 'datetime'}
)
p5.add_tools(h5)

show(column(p, p5, select))

#### Vs. Labour

In [13]:
p6 = figure(**figure_args, 
    title = 'Wage Rate Index',
    y_axis_label = 'Indices',
    x_range = p.x_range
)
p6.line('Time', 'Labor_Markets|Wage_Rates|Index', legend_label = 'Wage Rate Index', **line_args)

p6.legend.location = 'top_right'
p6.legend.click_policy = 'mute'

h6 = HoverTool(
    mode = 'vline',
    tooltips = [
        ('Time-Period', '@Time{%m/%Y}'),
        ('Wage Rate Index', '@{Labor_Markets|Wage_Rates|Index}'),
    ],
    formatters = {'@Time': 'datetime'}
)
p6.add_tools(h6)



p7 = figure(**figure_args, 
    title = 'Count of Unemployed Persons',
    y_axis_label = 'Population Count',
    x_range = p.x_range
)
p7.line('Time', 'Unemployment|Persons|Number_of', legend_label = 'Count of Unemployed Persons', **line_args)

p7.legend.location = 'top_right'
p7.legend.click_policy = 'mute'

h7 = HoverTool(
    mode = 'vline',
    tooltips = [
        ('Time-Period', '@Time{%m/%Y}'),
        ('Count of Unemployed Persons', '@{Unemployment|Persons|Number_of}'),
    ],
    formatters = {'@Time': 'datetime'}
)
p7.add_tools(h7)

show(column(p, p6, p7, select))

#### Vs. Interest Rates

##### Vs. Government's Direct Interventions

In [14]:
p8 = figure(**figure_args, 
    title = 'Central Bank and Government Intervention',
    y_axis_label = 'Interest Rates (Percentage)',
    x_range = p.x_range
)
p8.line('Time', 'Deposit_Rate', legend_label = 'Deposit Rate', **line_args)
p8.line('Time', 'Government_Bonds', legend_label = 'Government Bonds', **line_args)

p8.legend.location = 'top_right'
p8.legend.click_policy = 'mute'

h8 = HoverTool(
    mode = 'vline',
    tooltips = [
        ('Time-Period', '@Time{%m/%Y}'),
        ('Deposit Rate', '@Deposit_Rate'),
        ('Government Bonds', '@Government_Bonds'),
    ],
    formatters = {'@Time': 'datetime'}
)
p8.add_tools(h8)

show(column(p, p8, select))

##### Vs. Loans to Private Entities

In [15]:
p9 = figure(**figure_args, 
    title = 'Loans to Private Entities',
    y_axis_label = 'Interest Rates on Loans (Percentage)',
    x_range = p.x_range
)
p9.line('Time', 'Harmonized_Euro_Area_Rates|Loans|Households|Consumer_Credit_and_Other|Up_to_1_Year', legend_label = 'Consumer Credit', **line_args)
p9.line('Time', 'Harmonized_Euro_Area_Rates|Loans|Households|House_Purchase|Over_5_Years', legend_label = 'House Purchase', **line_args)
p9.line('Time', 'Harmonized_Euro_Area_Rates|Loans|Non-Financial_Corporations|Up_to_1_Year', legend_label = 'Non-financial Corps.', **line_args)

p9.legend.location = 'top_right'
p9.legend.click_policy = 'mute'

h9 = HoverTool(
    mode = 'vline',
    tooltips = [
        ('Time-Period', '@Time{%m/%Y}'),
        ('Consumer Credit', '@{Harmonized_Euro_Area_Rates|Loans|Households|Consumer_Credit_and_Other|Up_to_1_Year}'),
        ('House Purchase', '@{Harmonized_Euro_Area_Rates|Loans|Households|House_Purchase|Over_5_Years}'),
        ('Non-financial Corps.', '@{Harmonized_Euro_Area_Rates|Loans|Non-Financial_Corporations|Up_to_1_Year}')
    ],
    formatters = {'@Time': 'datetime'}
)
p9.add_tools(h9)

show(column(p, p9, select))

##### Vs. Returns on Debt Funds

In [16]:
p10 = figure(**figure_args, 
    title = 'Returns on Debt Funds',
    y_axis_label = 'Interest Rates on Deposits (Percentage)',
    x_range = p.x_range
)
p10.line('Time', 'Harmonized_Euro_Area_Rates|New_Business|Deposits|Households|Agreed_Maturity|Up_to_1_Year', legend_label = 'Households', **line_args)
p10.line('Time', 'Harmonized_Euro_Area_Rates|New_Business|Deposits|Non-financial_Corporations|Agreed_Maturity|Up_to_1_Year', legend_label = 'Non-financial Corps.', **line_args)

p10.legend.location = 'top_right'
p10.legend.click_policy = 'mute'

h10 = HoverTool(
    mode = 'vline',
    tooltips = [
        ('Time-Period', '@Time{%m/%Y}'),
        ('Households', '@{Harmonized_Euro_Area_Rates|New_Business|Deposits|Households|Agreed_Maturity|Up_to_1_Year}'),
        ('Non-financial Corps.', '@{Harmonized_Euro_Area_Rates|New_Business|Deposits|Non-financial_Corporations|Agreed_Maturity|Up_to_1_Year}'),
    ],
    formatters = {'@Time': 'datetime'}
)
p10.add_tools(h10)

show(column(p, p10, select))

##### Vs. Loans to Individuals

In [17]:
p11 = figure(**figure_args, 
    title = 'Loans to Individuals',
    y_axis_label = 'Interest Rates on Loans (Percentage)',
    x_range = p.x_range
)
p11.line('Time', 'Harmonized_Euro_Area_Rates|New_Business|Loans|Households|Consumption|Floating_Rate_and_up_to_1_Year', legend_label = 'Miscellaneous', **line_args)
p11.line('Time', 'Harmonized_Euro_Area_Rates|New_Business|Loans|Households|House_Purchase|Over_5_Years', legend_label = 'House Purchase', **line_args)

p11.legend.location = 'top_right'
p11.legend.click_policy = 'mute'

h11 = HoverTool(
    mode = 'vline',
    tooltips = [
        ('Time-Period', '@Time{%m/%Y}'),
        ('Miscellaneous', '@{Harmonized_Euro_Area_Rates|New_Business|Loans|Households|Consumption|Floating_Rate_and_up_to_1_Year}'),
        ('House Purchase', '@{Harmonized_Euro_Area_Rates|New_Business|Loans|Households|House_Purchase|Over_5_Years}'),
    ],
    formatters = {'@Time': 'datetime'}
)
p11.add_tools(h11)

show(column(p, p11, select))

##### Vs. Outstanding Loan Amounts

In [18]:
p12 = figure(**figure_args, 
    title = 'Outstanding Loan Amounts',
    y_axis_label = 'Amount (Euro)',
    x_range = p.x_range
)
p12.line('Time', 'Harmonized_Euro_Area_Rates|Outstanding_Amounts|Deposits|Households|Agreed_Maturity|Up_to_2_Years', legend_label = 'Households', **line_args)
p12.line('Time', 'Harmonized_Euro_Area_Rates|Outstanding_Amounts|Deposits|Non-Financial_Corporations|Agreed_Maturity|Up_to_2_Years', legend_label = 'Non-financial Corps.', **line_args)

p12.legend.location = 'top_right'
p12.legend.click_policy = 'mute'

h12 = HoverTool(
    mode = 'vline',
    tooltips = [
        ('Time-Period', '@Time{%m/%Y}'),
        ('Households', '@{Harmonized_Euro_Area_Rates|Outstanding_Amounts|Deposits|Households|Agreed_Maturity|Up_to_2_Years}'),
        ('Non-financial Corps.', '@{Harmonized_Euro_Area_Rates|Outstanding_Amounts|Deposits|Non-Financial_Corporations|Agreed_Maturity|Up_to_2_Years}'),
    ],
    formatters = {'@Time': 'datetime'}
)
p12.add_tools(h12)

show(column(p, p12, select))

### Vs. Confidence

In [19]:
p13 = figure(**figure_args, 
    title = 'Market Confidence',
    y_axis_label = 'Index',
    x_range = p.x_range
)
p13.line('Time', 'Business_Confidence', legend_label = 'Business Confidence', **line_args)
p13.line('Time', 'Consumer_Confidence', legend_label = 'Consumer Confidence', **line_args)

p13.legend.location = 'top_right'
p13.legend.click_policy = 'mute'

h13 = HoverTool(
    mode = 'vline',
    tooltips = [
        ('Time-Period', '@Time{%m/%Y}'),
        ('Households', '@Business_Confidence'),
        ('Non-financial Corps.', '@Consumer_Confidence'),
    ],
    formatters = {'@Time': 'datetime'}
)
p13.add_tools(h13)

show(column(p, p13, select))

### Vs. GDP

#### Vs. GDP Current/Nominal

##### Vs. GDP Current/Nominal, Unadjusted

In [22]:
p14 = figure(**figure_args, 
    title = 'GDP Figures (Trade) (Nominal, Unadjusted)',
    y_axis_label = 'Amount (Euro)',
    x_range = p.x_range
)
p14.line('Time', 'Change_in_Inventories|Nominal|Undjusted|Domestic_Currency', legend_label = 'Change in Inventories', **line_args)
p14.line('Time', 'Exports_of_Goods_and_Services|Nominal|Undjusted|Domestic_Currency', legend_label = 'Exports of Goods and Services', **line_args)
p14.line('Time', 'Imports_of_Goods_and_Services|Nominal|Undjusted|Domestic_Currency', legend_label = 'Imports of Goods and Services', **line_args)

p14.legend.location = 'top_right'
p14.legend.click_policy = 'mute'

h14 = HoverTool(
    mode = 'vline',
    tooltips = [
        ('Time-Period', '@Time{%m/%Y}'),
        ('Change in Inventories', '@{Change_in_Inventories|Nominal|Undjusted|Domestic_Currency}'),
        ('Exports of Goods and Services', '@{Exports_of_Goods_and_Services|Nominal|Undjusted|Domestic_Currency}'),
        ('Imports of Goods and Services', '@{Imports_of_Goods_and_Services|Nominal|Undjusted|Domestic_Currency}'),
    ],
    formatters = {'@Time': 'datetime'}
)
p14.add_tools(h14)



p15 = figure(**figure_args, 
    title = 'GDP Figures (Production and Consumption) (Nominal, Unadjusted)',
    y_axis_label = 'Amount (Euro)',
    x_range = p.x_range
)
p15.line('Time', 'Gross_Domestic_Product|Nominal|Undjusted|Domestic_Currency', legend_label = 'Gross Domestic Product', **line_args)
p15.line('Time', 'Household_Consumption_Expenditure|incl._NPISHs|Nominal|Undjusted|Domestic_Currency', legend_label = 'Household Consumption Expenditure', **line_args)
p15.line('Time', 'Government_Consumption_Expenditure|Nominal|Undjusted|Domestic_Currency', legend_label = 'Government Consumption Expenditure', **line_args)
p15.line('Time', 'Gross_Fixed_Capital_Formation|Nominal|Undjusted|Domestic_Currency', legend_label = 'Gross Fixed Capital Formation', **line_args)

p15.legend.location = 'top_right'
p15.legend.click_policy = 'mute'

h15 = HoverTool(
    mode = 'vline',
    tooltips = [
        ('Time-Period', '@Time{%m/%Y}'),
        ('Gross Domestic Product', '@{Gross_Domestic_Product|Nominal|Undjusted|Domestic_Currency}'),
        ('Household Consumption Expenditure', '@{Household_Consumption_Expenditure|incl._NPISHs|Nominal|Undjusted|Domestic_Currency}'),
        ('Government Consumption Expenditure', '@{Government_Consumption_Expenditure|Nominal|Undjusted|Domestic_Currency}'),
        ('Gross Fixed Capital Formation', '@{Gross_Fixed_Capital_Formation|Nominal|Undjusted|Domestic_Currency}'),
    ],
    formatters = {'@Time': 'datetime'}
)
p15.add_tools(h15)



show(column(p, p14, p15, select))

##### Vs. GDP Current/Nominal, Seasonally Adjusted

In [24]:
p16 = figure(**figure_args, 
    title = 'GDP Figures (Trade) (Current/Nominal, Seasonally Adjusted)',
    y_axis_label = 'Amount (Euro)',
    x_range = p.x_range
)
p16.line('Time', 'Change_in_Inventories|Nominal|Seasonally_Adjusted|Domestic_Currency', legend_label = 'Change in Inventories', **line_args)
p16.line('Time', 'Exports_of_Goods_and_Services|Nominal|Seasonally_Adjusted|Domestic_Currency', legend_label = 'Exports of Goods and Services', **line_args)
p16.line('Time', 'Imports_of_Goods_and_Services|Nominal|Seasonally_Adjusted|Domestic_Currency', legend_label = 'Imports of Goods and Services', **line_args)

p16.legend.location = 'top_right'
p16.legend.click_policy = 'mute'

h16 = HoverTool(
    mode = 'vline',
    tooltips = [
        ('Time-Period', '@Time{%m/%Y}'),
        ('Change in Inventories', '@{Change_in_Inventories|Nominal|Seasonally_Adjusted|Domestic_Currency}'),
        ('Exports of Goods and Services', '@{Exports_of_Goods_and_Services|Nominal|Seasonally_Adjusted|Domestic_Currency}'),
        ('Imports of Goods and Services', '@{Imports_of_Goods_and_Services|Nominal|Seasonally_Adjusted|Domestic_Currency}'),
    ],
    formatters = {'@Time': 'datetime'}
)
p16.add_tools(h16)



p17 = figure(**figure_args, 
    title = 'GDP Figures (Production and Consumption) (Current/Nominal, Seasonally Adjusted)',
    y_axis_label = 'Amount (Euro)',
    x_range = p.x_range
)
p17.line('Time', 'Gross_Domestic_Product|Nominal|Seasonally_Adjusted|Domestic_Currency', legend_label = 'Gross Domestic Product', **line_args)
p17.line('Time', 'Household_Consumption_Expenditure|incl._NPISHs|Nominal|Seasonally_Adjusted|Domestic_Currency', legend_label = 'Household Consumption Expenditure', **line_args)
p17.line('Time', 'Government_Final_Consumption_Expenditure|Nominal|Seasonally_adjusted|Domestic_Currency', legend_label = 'Government Consumption Expenditure', **line_args)
p17.line('Time', 'Gross_Fixed_Capital_Formation|Nominal|Seasonally_Adjusted|Domestic_Currency', legend_label = 'Gross Fixed Capital Formation', **line_args)

p17.legend.location = 'top_right'
p17.legend.click_policy = 'mute'

h17 = HoverTool(
    mode = 'vline',
    tooltips = [
        ('Time-Period', '@Time{%m/%Y}'),
        ('Gross Domestic Product', '@{Gross_Domestic_Product|Nominal|Seasonally_Adjusted|Domestic_Currency}'),
        ('Household Consumption Expenditure', '@{Household_Consumption_Expenditure|incl._NPISHs|Nominal|Seasonally_Adjusted|Domestic_Currency}'),
        ('Government Consumption Expenditure', '@{Government_Final_Consumption_Expenditure|Nominal|Seasonally_adjusted|Domestic_Currency}'),
        ('Gross Fixed Capital Formation', '@{Gross_Fixed_Capital_Formation|Nominal|Seasonally_Adjusted|Domestic_Currency}'),
    ],
    formatters = {'@Time': 'datetime'}
)
p17.add_tools(h17)



show(column(p, p16, p17, select))

#### Vs. GDP Constant

##### Vs. GDP Constant, Unadjusted

In [25]:
p18 = figure(**figure_args, 
    title = 'GDP Figures (Trade) (Base Year->2010, Unadjusted)',
    y_axis_label = 'Amount (Euro)',
    x_range = p.x_range
)
p18.line('Time', 'Change_in_Inventories|Real|Undjusted|Domestic_Currency|Base_Year-2010.0', legend_label = 'Change in Inventories', **line_args)
p18.line('Time', 'Exports_of_Goods_and_Services|Real|Undjusted|Domestic_Currency|Base_Year-2010.0', legend_label = 'Exports of Goods and Services', **line_args)
p18.line('Time', 'Imports_of_Goods_and_Services|Real|Undjusted|Domestic_Currency|Base_Year-2010.0', legend_label = 'Imports of Goods and Services', **line_args)

p18.legend.location = 'top_right'
p18.legend.click_policy = 'mute'

h18 = HoverTool(
    mode = 'vline',
    tooltips = [
        ('Time-Period', '@Time{%m/%Y}'),
        ('Change in Inventories', '@{Change_in_Inventories|Real|Undjusted|Domestic_Currency|Base_Year-2010.0}'),
        ('Exports of Goods and Services', '@{Exports_of_Goods_and_Services|Real|Undjusted|Domestic_Currency|Base_Year-2010.0}'),
        ('Imports of Goods and Services', '@{Imports_of_Goods_and_Services|Real|Undjusted|Domestic_Currency|Base_Year-2010.0}'),
    ],
    formatters = {'@Time': 'datetime'}
)
p18.add_tools(h18)



p19 = figure(**figure_args, 
    title = 'GDP Figures (Production and Consumption) (Base Year->2010, Unadjusted)',
    y_axis_label = 'Amount (Euro)',
    x_range = p.x_range
)
p19.line('Time', 'Gross_Domestic_Product|Real|Undjusted|Domestic_Currency|Base_Year-2010.0', legend_label = 'Gross Domestic Product', **line_args)
p19.line('Time', 'Household_Consumption_Expenditure|incl._NPISHs|Real|Undjusted|Domestic_Currency|Base_Year-2010.0', legend_label = 'Household Consumption Expenditure', **line_args)
p19.line('Time', 'Government_Consumption_Expenditure|Real|Undjusted|Domestic_Currency|Base_Year-2010.0', legend_label = 'Government Consumption Expenditure', **line_args)
p19.line('Time', 'Gross_Fixed_Capital_Formation|Real|Undjusted|Domestic_Currency|Base_Year-2010.0', legend_label = 'Gross Fixed Capital Formation', **line_args)

p19.legend.location = 'top_right'
p19.legend.click_policy = 'mute'

h19 = HoverTool(
    mode = 'vline',
    tooltips = [
        ('Time-Period', '@Time{%m/%Y}'),
        ('Gross Domestic Product', '@{Gross_Domestic_Product|Real|Undjusted|Domestic_Currency|Base_Year-2010.0}'),
        ('Household Consumption Expenditure', '@{Household_Consumption_Expenditure|incl._NPISHs|Real|Undjusted|Domestic_Currency|Base_Year-2010.0}'),
        ('Government Consumption Expenditure', '@{Government_Consumption_Expenditure|Real|Undjusted|Domestic_Currency|Base_Year-2010.0}'),
        ('Gross Fixed Capital Formation', '@{Gross_Fixed_Capital_Formation|Real|Undjusted|Domestic_Currency|Base_Year-2010.0}'),
    ],
    formatters = {'@Time': 'datetime'}
)
p19.add_tools(h19)



show(column(p, p18, p19, select))

##### Vs. GDP Constant, Seasonally Adjusted

In [27]:
p20 = figure(**figure_args, 
    title = 'GDP Figures (Trade) (Base Year->2010, Seasonally Adjusted)',
    y_axis_label = 'Amount (Euro)',
    x_range = p.x_range
)
p20.line('Time', 'Change_in_Inventories|Real|Seasonally_Adjusted|Domestic_Currency|Base_Year-2010.0', legend_label = 'Change in Inventories', **line_args)
p20.line('Time', 'Exports_of_Goods_and_Services|Real|Seasonally_Adjusted|Domestic_Currency|Base_Year-2010.0', legend_label = 'Exports of Goods and Services', **line_args)
p20.line('Time', 'Imports_of_Goods_and_Services|Real|Seasonally_Adjusted|Domestic_Currency|Base_Year-2010.0', legend_label = 'Imports of Goods and Services', **line_args)

p20.legend.location = 'top_right'
p20.legend.click_policy = 'mute'

h20 = HoverTool(
    mode = 'vline',
    tooltips = [
        ('Time-Period', '@Time{%m/%Y}'),
        ('Change in Inventories', '@{Change_in_Inventories|Real|Seasonally_Adjusted|Domestic_Currency|Base_Year-2010.0}'),
        ('Exports of Goods and Services', '@{Exports_of_Goods_and_Services|Real|Seasonally_Adjusted|Domestic_Currency|Base_Year-2010.0}'),
        ('Imports of Goods and Services', '@{Imports_of_Goods_and_Services|Real|Seasonally_Adjusted|Domestic_Currency|Base_Year-2010.0}'),
    ],
    formatters = {'@Time': 'datetime'}
)
p20.add_tools(h20)



p21 = figure(**figure_args, 
    title = 'GDP Figures (Production and Consumption) (Base Year->2010, Seasonally Adjusted)',
    y_axis_label = 'Amount (Euro)',
    x_range = p.x_range
)
p21.line('Time', 'Gross_Domestic_Product|Real|Seasonally_Adjusted|Domestic_Currency|Base_Year-2010.0', legend_label = 'Gross Domestic Product', **line_args)
p21.line('Time', 'Household_Consumption_Expenditure|incl._NPISHs|Real|Seasonally_Adjusted|Domestic_Currency|Base_Year-2010.0', legend_label = 'Household Consumption Expenditure', **line_args)
p21.line('Time', 'Government_Final_Consumption_Expenditure|Real|Seasonally_adjusted|Domestic_Currency|Base_Year-2010.0', legend_label = 'Government Consumption Expenditure', **line_args)
p21.line('Time', 'Gross_Fixed_Capital_Formation|Real|Seasonally_Adjusted|Domestic_Currency|Base_Year-2010.0', legend_label = 'Gross Fixed Capital Formation', **line_args)

p21.legend.location = 'top_right'
p21.legend.click_policy = 'mute'

h21 = HoverTool(
    mode = 'vline',
    tooltips = [
        ('Time-Period', '@Time{%m/%Y}'),
        ('Gross Domestic Product', '@{Gross_Domestic_Product|Real|Seasonally_Adjusted|Domestic_Currency|Base_Year-2010.0}'),
        ('Household Consumption Expenditure', '@{Household_Consumption_Expenditure|incl._NPISHs|Real|Seasonally_Adjusted|Domestic_Currency|Base_Year-2010.0}'),
        ('Government Consumption Expenditure', '@{Government_Final_Consumption_Expenditure|Real|Seasonally_adjusted|Domestic_Currency|Base_Year-2010.0}'),
        ('Gross Fixed Capital Formation', '@{Gross_Fixed_Capital_Formation|Real|Seasonally_Adjusted|Domestic_Currency|Base_Year-2010.0}'),
    ],
    formatters = {'@Time': 'datetime'}
)
p21.add_tools(h21)



p22 = figure(**figure_args, 
    title = 'GDP Figures (Deflator) (Base Year->2010, Seasonally Adjusted)',
    y_axis_label = 'Index',
    x_range = p.x_range
)
p22.line('Time', 'Gross_Domestic_Product|Deflator|Seasonally_Adjusted|Base_Year-2010.0', legend_label = 'GDP Deflator', **line_args)

p22.legend.location = 'top_right'
p22.legend.click_policy = 'mute'

h22 = HoverTool(
    mode = 'vline',
    tooltips = [
        ('Time-Period', '@Time{%m/%Y}'),
        ('GDP Deflator', '@{Gross_Domestic_Product|Deflator|Seasonally_Adjusted|Base_Year-2010.0}'),
    ],
    formatters = {'@Time': 'datetime'}
)
p22.add_tools(h22)



show(column(p, p20, p21, p22, select))